In [1]:
from geopy.distance import distance
import geopandas as gpd
import datetime
import numpy as np

file = '/home/conor/Projects/D4D/data/connor_2020-02-23T16_50_40-07_00.geojson'

## Load each point in the geojson file into a pandas dataframe and create new columns for the ```coordinates``` of each point and the ```timestamp``` as a ```datetime``` object - ```timestamp_dt```

In [2]:
df = gpd.read_file(file)

def f_coords(x):
    b = x.bounds
    return (b[1], b[0])

df['coordinates'] = df['geometry'].apply(f_coords)

df["timestamp_dt"] = df["timestamp"].apply(lambda x: datetime.datetime.strptime(x, "%Y-%m-%dT%H:%M:%S"))

In [3]:
df.sort_values(by="timestamp_dt", ascending=True)

algorithm  background_maximum_return  background_mean_return  \
4248  ACD-29August2019                       3.36                    1.27   
4249  ACD-29August2019                       5.41                    2.59   
4250  ACD-29August2019                      11.84                    6.30   
4251  ACD-29August2019                       7.58                    3.16   
4252  ACD-29August2019                      12.07                    4.11   
...                ...                        ...                     ...   
4218  ACD-29August2019                       1.82                    0.71   
4219  ACD-29August2019                       2.28                    1.59   
4220  ACD-29August2019                       6.27                    1.34   
4222  ACD-29August2019                      14.63                    7.20   
4246  ACD-29August2019                       5.73                    3.76   

      background_minimum_return  centroid_lat  centroid_lon  change_area  \
4248                       0.04     31.592990     43.936550       526.00   
4249                       0.00     31.833372     43.656004       282.82   
4250                       1.05     31.879711     43.713683       329.95   
4251                       0.29     32.835074     41.327486       479.16   
4252                       0.00     32.502141     41.416089       359.23   
...                         ...           ...           ...          ...   
4218                       0.23     31.007855     42.221301       422.92   
4219                       0.45     31.022819     42.367975       281.94   
4220                       0.28     31.075552     42.526360       328.93   
4222                       0.33     30.996824     42.574917       328.93   
4246                       0.92     32.711101     42.416815       282.21   

      compactness  detect_strength detect_type  ...  target_maximum_return  \
4248       1.0776            -30.9   Departure  ...                2208.82   
4249       0.9842            -24.7   Departure  ...                 996.42   
4250       1.0846            -23.7   Departure  ...                1416.18   
4251       1.6634            -16.2   Departure  ...                 259.53   
4252       1.0462            -27.2   Departure  ...                 303.04   
...           ...              ...         ...  ...                    ...   
4218       0.9998             40.0     Arrival  ...               12574.07   
4219       1.0310             29.0     Arrival  ...                 502.72   
4220       1.0716             27.2     Arrival  ...                 904.40   
4222       1.0846             23.2     Arrival  ...                1329.47   
4246       1.3880             21.5     Arrival  ...                 501.90   

     target_mean_return target_minimum_return  target_total_return  \
4248             773.52                 36.16              7735.24   
4249             512.43                334.74              3074.55   
4250             661.18                126.76              4628.25   
4251             151.28                 51.83              1210.21   
4252             161.45                 60.37               968.68   
...                 ...                   ...                  ...   
4218            3746.76                 37.01             33720.83   
4219             295.57                 48.38              1773.42   
4220             385.43                 38.03              2698.03   
4222             494.65                105.10              3462.54   
4246             301.54                 62.48              1809.24   

                timestamp weighted_centroid_lat  weighted_centroid_lon  \
4248  2018-11-01T00:00:00             31.592985              43.936581   
4249  2018-11-01T00:00:00             31.833377              43.656003   
4250  2018-11-01T00:00:00             31.879723              43.713676   
4251  2018-11-05T00:00:00             32.835112              41.327497   
4252  2018-11-05T00:00:00  

## ```dts``` in the following cell will be a list of unique ```datetime``` objects from geojson file##

In [4]:
list_dts = df["timestamp_dt"].to_list()
np_dts = np.array(list_dts)
dts = np.unique(np_dts)

In [5]:
class Cluster:
    def __init__(self, coords, time, size):
        self.coords = coords
        self.time = time
        self.size = size
    def new_point(self, coord):
        self.coords.append(coord)
        self.size += 1
    def print_cluster(self):
        print("Date of cluster: ", end = " ")
        print(self.time)
        print("Size of cluster: ", end = " ")
        print(self.size)
        print("Point within collect: ")
        for coord in self.coords:
            print(coord.get_coords())
    def get_coords(self):
        return self.coords
    def add_coords(self, coords):
        self.coords.extend(coords)
    
    # functions used to make circles
    def make_centroid(self):
        tot_lat = 0
        tot_lon = 0
        for coord in self.coords:
            c = coord.get_coords()
            tot_lat += c[0]
            tot_lon += c[1]
        lat = tot_lat / len(self.coords)
        lon = tot_lon / len(self.coords)
        self.centroid = (lat, lon)
    def get_centroid(self):
        return self.centroid
    def make_radii(self):
        dist_sum = 0
        dist_max = 0
        for coord in self.coords:
            c = coord.get_coords()
            dist = distance(c, self.centroid).km
            if dist > dist_max:
                dist_max = dist
            dist_sum += dist
        self.max_r = dist_max
        self.avg_r = dist_sum / len(self.coords)
    def get_max_r(self):
        return self.max_r
    def get_avg_r(self):
        return self.avg_r

In [23]:
class Collect(Cluster):
    def __init__(self, coords, time, num, clusters):
        self.coords = coords
        self.time = time
        self.num = num
        self.clusters = clusters
    def print_collect(self):
        print("Date of collect: ", end = " ") 
        print(self.time)
        print("Number of points in collect: ", end = " ") 
        print(self.num)
        print("Coordinates of points: ", end = " ") 
        print(self.coords)
    def get_coords(self):
        return self.coords
    def get_time(self):
        return self.time
    def get_clusters(self):
        return self.clusters
    def get_cluster(self, i):
        return self.clusters[i]
    def combine_clusters(self, i1, i2):
        c_list = self.clusters[i2].get_coords()
        self.clusters[i1].add_coords(c_list)
        dup_clust = self.clusters[i2]
        self.clusters.remove(dup_clust)
    def add_to_cluster(self, i, cc):
        self.clusters[i].new_point(cc)
    def add_cluster(self, cc):
        self.clusters.append(Cluster(cc, self.time, 2))
    def print_clusters(self):
        idx = 0
        for cluster in self.clusters:
            print("Index in clusters array: " + str(idx))
            self.clusters[idx].print_cluster()
            idx += 1
            print()
    def print_cluster_distances(self):
        idx = 0
        for cluster in self.clusters:
            print("INDEX OF CLUSTER IN ARRAY: " + str(idx))
            coords = cluster.get_coords()
            for i in range(len(coords)):
                for j in range(len(coords)):
                    if i < j:
                        print("Points " + str(i) + " and " + str(j))
                        print("First point: " + str(coords[i].get_coords()))
                        print("Second point: " + str(coords[j].get_coords()))
                        dist = distance(coords[i].get_coords(), coords[j].get_coords()).km
                        print("Distance in km between the points: " + str(dist))
                        print()
            idx += 1
    def make_circle_properties(self):
        for cluster in self.clusters:
            cluster.make_centroid()
            cluster.make_radii()
            print(cluster.get_centroid())
            print(cluster.get_max_r())
            print(cluster.get_avg_r())
            print()
            
    def debug(self):
        clust1 = self.get_cluster(16)
        clust2 = self.get_cluster(17)
        coords1 = clust1.get_coords()
        coords2 = clust2.get_coords()
        for i in range(len(coords1)):
                for j in range(len(coords2)):
                    print("Points " + str(i) + " and " + str(j))
                    print("First point: " + str(coords1[i].get_coords()))
                    print("Second point: " + str(coords2[j].get_coords()))
                    dist = distance(coords1[i].get_coords(), coords2[j].get_coords()).km
                    print("Distance in km between the points: " + str(dist))
                    print()

In [7]:
# built to keep track of whether a set of coordinates is already in a cluster with c

class Cluster_Coord:
    def __init__(self, coords, c):
        self.coords = coords
        self.c = c
    def change_status(self, c):
        self.c = c
    def get_status(self):
        return self.c
    def get_coords(self):
        return self.coords

In [8]:
collects = [] # list of collects

In [9]:
def init_collect(time):
    coords = []
    collect_data = df.loc[df['timestamp_dt']==time, ['coordinates', 'timestamp_dt']]
    num = len(collect_data)
    for i in range(num):
        d = collect_data.iloc[i,:]
        coords.append(d[0])
    clusters = []
    collects.append(Collect(coords, time, num, clusters))

In [10]:
# initialize all of the collects to the collects array - can be different time period down the line

for time in dts:
    init_collect(time)

idx = 0
for collect in collects:
    print("Index of collects array: " + str(idx))
    idx += 1
    collect.print_collect()
    print()

Index of collects array: 0
Date of collect:  2018-11-01 00:00:00
Number of points in collect:  3
Coordinates of points:  [(31.5931135, 43.9365099), (31.8334953, 43.6559675), (31.8798349, 43.7136467)]

Index of collects array: 1
Date of collect:  2018-11-05 00:00:00
Number of points in collect:  4
Coordinates of points:  [(32.8351977, 41.3274391), (32.5022643, 41.4160425), (32.4978841, 41.4141477), (32.4518448, 41.37964)]

Index of collects array: 2
Date of collect:  2018-11-06 00:00:00
Number of points in collect:  23
Coordinates of points:  [(32.7993297, 42.8858036), (32.3368143, 43.319328), (32.3849988, 43.3193711), (32.384144, 43.3173443), (32.3437482, 43.3284922), (32.343872, 43.3279943), (32.3373096, 43.3204349), (32.3439545, 43.3276754), (31.5390979, 43.4076214), (32.431786, 42.1213852), (32.4875081, 42.1089776), (32.2772893, 42.209378), (32.0276532, 42.3203179), (32.0953926, 42.5449025), (32.0901751, 42.5058812), (32.0380529, 42.2591599), (31.5625085, 42.1659556), (31.5403554, 4

## The following two cells are to show the distances between each point in a collect. This distance is used to form clusters

In [11]:
def print_collect_distances(collect):
    coords = collect.get_coords()
    for i in range(len(coords)):
        for j in range(len(coords)):
            if i < j:
                print("Points " + str(i) + " and " + str(j))
                print("First point: " + str(coords[i]))
                print("Second point: " + str(coords[j]))
                dist = distance(coords[i], coords[j]).km
                print("Distance in km between the points: " + str(dist))
                print()

In [12]:
print_collect_distances(collects[76])

Points 0 and 1
First point: (30.7524522, 42.0460538)
Second point: (30.8223067, 41.9621215)
Distance in km between the points: 11.15867301762634

Points 0 and 2
First point: (30.7524522, 42.0460538)
Second point: (30.8022632, 42.1143506)
Distance in km between the points: 8.557929568286328

Points 0 and 3
First point: (30.7524522, 42.0460538)
Second point: (30.8842179, 41.9287493)
Distance in km between the points: 18.422506335249103

Points 0 and 4
First point: (30.7524522, 42.0460538)
Second point: (30.8598343, 42.0465252)
Distance in km between the points: 11.905124264138555

Points 0 and 5
First point: (30.7524522, 42.0460538)
Second point: (30.8334742, 41.9525127)
Distance in km between the points: 12.682255137123581

Points 0 and 6
First point: (30.7524522, 42.0460538)
Second point: (30.9126577, 41.8913186)
Distance in km between the points: 23.121760295619335

Points 0 and 7
First point: (30.7524522, 42.0460538)
Second point: (30.8699195, 41.9728586)
Distance in km between the p

Points 1 and 11
First point: (30.8223067, 41.9621215)
Second point: (30.226213, 42.6672578)
Distance in km between the points: 94.58825427612737

Points 1 and 12
First point: (30.8223067, 41.9621215)
Second point: (30.240869, 42.6537853)
Distance in km between the points: 92.52486217598081

Points 1 and 13
First point: (30.8223067, 41.9621215)
Second point: (30.34833, 42.4239043)
Distance in km between the points: 68.72298697892546

Points 1 and 14
First point: (30.8223067, 41.9621215)
Second point: (30.3823146, 42.4879344)
Distance in km between the points: 70.15673454137537

Points 1 and 15
First point: (30.8223067, 41.9621215)
Second point: (30.3643628, 42.4045044)
Distance in km between the points: 66.16311593314902

Points 1 and 16
First point: (30.8223067, 41.9621215)
Second point: (30.3069172, 42.7767516)
Distance in km between the points: 96.81040935316048

Points 1 and 17
First point: (30.8223067, 41.9621215)
Second point: (30.5349312, 42.3380886)
Distance in km between the po

Distance in km between the points: 179.1287766040232

Points 2 and 81
First point: (30.8022632, 42.1143506)
Second point: (32.6037045, 42.3085688)
Distance in km between the points: 200.5933749967952

Points 2 and 82
First point: (30.8022632, 42.1143506)
Second point: (32.7214156, 42.0597764)
Distance in km between the points: 212.8635798577441

Points 2 and 83
First point: (30.8022632, 42.1143506)
Second point: (33.2468148, 42.4302304)
Distance in km between the points: 272.70676160677743

Points 2 and 84
First point: (30.8022632, 42.1143506)
Second point: (33.2219464, 42.3904333)
Distance in km between the points: 269.5761808620432

Points 2 and 85
First point: (30.8022632, 42.1143506)
Second point: (33.202728, 42.3766659)
Distance in km between the points: 267.3313393524714

Points 2 and 86
First point: (30.8022632, 42.1143506)
Second point: (33.2321948, 42.3516948)
Distance in km between the points: 270.37938028138757

Points 2 and 87
First point: (30.8022632, 42.1143506)
Second po

First point: (30.8842179, 41.9287493)
Second point: (30.3483163, 42.4238983)
Distance in km between the points: 76.05116805330687

Points 3 and 107
First point: (30.8842179, 41.9287493)
Second point: (30.364338, 42.4045179)
Distance in km between the points: 73.50205292427921

Points 3 and 108
First point: (30.8842179, 41.9287493)
Second point: (30.3322372, 42.7407522)
Distance in km between the points: 99.03306981210632

Points 3 and 109
First point: (30.8842179, 41.9287493)
Second point: (30.5349788, 42.3380786)
Distance in km between the points: 55.10502971670262

Points 3 and 110
First point: (30.8842179, 41.9287493)
Second point: (30.4819663, 42.4129952)
Distance in km between the points: 64.35567772734122

Points 3 and 111
First point: (30.8842179, 41.9287493)
Second point: (30.382287, 42.4879534)
Distance in km between the points: 77.26831615379928

Points 3 and 112
First point: (30.8842179, 41.9287493)
Second point: (30.4056588, 42.3627575)
Distance in km between the points: 67

Second point: (30.481971, 42.4129877)
Distance in km between the points: 58.87560485604616

Points 5 and 19
First point: (30.8334742, 41.9525127)
Second point: (30.3823467, 42.4879454)
Distance in km between the points: 71.67643246142804

Points 5 and 20
First point: (30.8334742, 41.9525127)
Second point: (30.4055948, 42.3627582)
Distance in km between the points: 61.622952359704215

Points 5 and 21
First point: (30.8334742, 41.9525127)
Second point: (30.5190582, 42.3421302)
Distance in km between the points: 51.07787581651822

Points 5 and 22
First point: (30.8334742, 41.9525127)
Second point: (30.6323132, 42.2277947)
Distance in km between the points: 34.53118842675463

Points 5 and 23
First point: (30.8334742, 41.9525127)
Second point: (30.6588956, 42.2703281)
Distance in km between the points: 36.066022332821774

Points 5 and 24
First point: (30.8334742, 41.9525127)
Second point: (30.5914154, 42.3883806)
Distance in km between the points: 49.632124621263635

Points 5 and 25
First p

...


Points 137 and 145
First point: (30.6992845, 42.2417019)
Second point: (31.0070162, 42.6478727)
Distance in km between the points: 51.70425130982354

Points 137 and 146
First point: (30.6992845, 42.2417019)
Second point: (31.3919967, 41.4600229)
Distance in km between the points: 107.07995557765774

Points 137 and 147
First point: (30.6992845, 42.2417019)
Second point: (31.4365166, 41.7040127)
Distance in km between the points: 96.50994316072696

Points 137 and 148
First point: (30.6992845, 42.2417019)
Second point: (31.440536, 41.8295549)
Distance in km between the points: 91.11035191011936

Points 137 and 149
First point: (30.6992845, 42.2417019)
Second point: (31.3846906, 41.4559396)
Distance in km between the points: 106.77591984917656

Points 137 and 150
First point: (30.6992845, 42.2417019)
Second point: (31.3846928, 41.4586642)
Distance in km between the points: 106.59354028569919

Points 137 and 151
First point: (30.6992845, 42.2417019)
Second point: (31.2970346, 42.3840585)
D

Distance in km between the points: 57.442083428070916

Points 142 and 146
First point: (30.6871047, 42.1755077)
Second point: (31.3919967, 41.4600229)
Distance in km between the points: 103.79258691047582

Points 142 and 147
First point: (30.6871047, 42.1755077)
Second point: (31.4365166, 41.7040127)
Distance in km between the points: 94.4910907480189

Points 142 and 148
First point: (30.6871047, 42.1755077)
Second point: (31.440536, 41.8295549)
Distance in km between the points: 89.82189370422778

Points 142 and 149
First point: (30.6871047, 42.1755077)
Second point: (31.3846906, 41.4559396)
Distance in km between the points: 103.44421084714502

Points 142 and 150
First point: (30.6871047, 42.1755077)
Second point: (31.3846928, 41.4586642)
Distance in km between the points: 103.2718435779139

Points 142 and 151
First point: (30.6871047, 42.1755077)
Second point: (31.2970346, 42.3840585)
Distance in km between the points: 70.49517377690893

Points 142 and 152
First point: (30.6871047, 

Points 149 and 173
First point: (31.3846906, 41.4559396)
Second point: (32.5074236, 42.210618)
Distance in km between the points: 143.49228009211907

Points 149 and 174
First point: (31.3846906, 41.4559396)
Second point: (32.4406061, 41.9616406)
Distance in km between the points: 126.47778357325299

Points 149 and 175
First point: (31.3846906, 41.4559396)
Second point: (32.4153469, 41.9565522)
Distance in km between the points: 123.70672352645812

Points 149 and 176
First point: (31.3846906, 41.4559396)
Second point: (32.604349, 42.3086298)
Distance in km between the points: 157.42679846144046

Points 149 and 177
First point: (31.3846906, 41.4559396)
Second point: (33.2219161, 42.390434)
Distance in km between the points: 221.9279359565485

Points 149 and 178
First point: (31.3846906, 41.4559396)
Second point: (33.2467639, 42.4302543)
Distance in km between the points: 225.95186271542454

Points 149 and 179
First point: (31.3846906, 41.4559396)
Second point: (33.1574357, 42.4663206)
Di


Points 157 and 169
First point: (31.402016, 42.5923136)
Second point: (32.0372168, 42.5345007)
Distance in km between the points: 70.64510396645115

Points 157 and 170
First point: (31.402016, 42.5923136)
Second point: (32.1426977, 42.4809071)
Distance in km between the points: 82.8040988790079

Points 157 and 171
First point: (31.402016, 42.5923136)
Second point: (32.3211247, 42.3096563)
Distance in km between the points: 105.36658666591964

Points 157 and 172
First point: (31.402016, 42.5923136)
Second point: (32.3206915, 42.3101168)
Distance in km between the points: 105.30907914635593

Points 157 and 173
First point: (31.402016, 42.5923136)
Second point: (32.5074236, 42.210618)
Distance in km between the points: 127.77524092906697

Points 157 and 174
First point: (31.402016, 42.5923136)
Second point: (32.4406061, 41.9616406)
Distance in km between the points: 129.69266349204312

Points 157 and 175
First point: (31.402016, 42.5923136)
Second point: (32.4153469, 41.9565522)
Distance

Points 170 and 177
First point: (32.1426977, 42.4809071)
Second point: (33.2219161, 42.390434)
Distance in km between the points: 119.98444852782112

Points 170 and 178
First point: (32.1426977, 42.4809071)
Second point: (33.2467639, 42.4302543)
Distance in km between the points: 122.5319888779489

Points 170 and 179
First point: (32.1426977, 42.4809071)
Second point: (33.1574357, 42.4663206)
Distance in km between the points: 112.54099989271123

Points 171 and 172
First point: (32.3211247, 42.3096563)
Second point: (32.3206915, 42.3101168)
Distance in km between the points: 0.06471443282975126

Points 171 and 173
First point: (32.3211247, 42.3096563)
Second point: (32.5074236, 42.210618)
Distance in km between the points: 22.662801711830536

Points 171 and 174
First point: (32.3211247, 42.3096563)
Second point: (32.4406061, 41.9616406)
Distance in km between the points: 35.32722655670927

Points 171 and 175
First point: (32.3211247, 42.3096563)
Second point: (32.4153469, 41.9565522)
D

In [13]:
def find_cluster(collect, cc): #pass in 2 cluster_coords
    for i in range(len(collect.get_clusters())):
        for point in collect.get_cluster(i).get_coords():
            if point == cc:
                return i
    return -1

In [14]:
def form_clusters_by_collect(collect, km_dist):
    cc = []
    coords = collect.get_coords()
    #init Cluster_Coords
    for coord in coords:
        cc.append(Cluster_Coord(coord, False))
    for i in range(len(cc)):
        for j in range(len(cc)):
            if (j > i):
                c1 = cc[i].get_coords()
                c2 = cc[j].get_coords()
                dist = distance(c1, c2).km
                if dist <= km_dist:
                    if cc[i].get_status() == True and cc[j].get_status() == True:
                        # check if in same cluster
                        clust1 = find_cluster(collect, cc[i])
                        clust2 = find_cluster(collect, cc[j])
                        if clust1 != clust2:
                            # concatenate clusters
                            
                            collect.combine_clusters(clust1, clust2)
                            
#                             idx1 = -1
#                             idx1 = clusters.index(clust1)
#                             idx2 = -1
#                             idx2 = clusters.index(clust2)
#                             if idx != -1:
#                                 c_list = clusters[idx2].get_coords()
#                                 clusters[idx1].add_coords(c_list)
#                                 clusters.remove(clust2)
                                
                        # else do nothing - already in a cluster together
                        
                    elif cc[i].get_status() == True and cc[j].get_status() == False:
                        clust = find_cluster(collect, cc[i])
                        collect.add_to_cluster(clust, cc[j])
#                         clusters[idx].new_point(cc[j])
                        cc[j].change_status(True)
                        
                    elif cc[i].get_status() == False and cc[j].get_status() == True:
                        clust = find_cluster(collect, cc[j])
                        collect.add_to_cluster(clust, cc[i])
#                         clusters[idx].new_point(cc[i])
                        cc[i].change_status(True)
                        
                    else: 
                        # create new cluster (size of 2 because every cluster starts with 2 points)
                        collect.add_cluster([cc[i], cc[j]])
#                         clusters.append(Cluster([cc[i], cc[j]], collect.get_time(), 2))
                        cc[i].change_status(True)
                        cc[j].change_status(True)

In [15]:
form_clusters_by_collect(collects[76], 10)

collects[76].print_clusters()

Index in clusters array: 0
Date of cluster:  2019-03-16 00:00:00
Size of cluster:  2
Point within collect: 
(29.8699546, 43.1158639)
(29.8699281, 43.1158783)
(29.9167578, 43.026635)
(29.9185782, 43.0774445)
(29.9168138, 43.0266163)
(29.922788, 43.1119457)

Index in clusters array: 1
Date of cluster:  2019-03-16 00:00:00
Size of cluster:  2
Point within collect: 
(29.9948947, 42.8171833)
(30.0027585, 42.8358367)

Index in clusters array: 2
Date of cluster:  2019-03-16 00:00:00
Size of cluster:  3
Point within collect: 
(30.226213, 42.6672578)
(30.240869, 42.6537853)
(30.2409008, 42.6537777)

Index in clusters array: 3
Date of cluster:  2019-03-16 00:00:00
Size of cluster:  2
Point within collect: 
(30.3069172, 42.7767516)
(30.3322372, 42.7407522)

Index in clusters array: 4
Date of cluster:  2019-03-16 00:00:00
Size of cluster:  36
Point within collect: 
(30.6323132, 42.2277947)
(30.6588956, 42.2703281)
(30.6454179, 42.2345359)
(30.6991743, 42.2417152)
(30.6403444, 42.3132286)
(30.63105

## As I did with collects, I now list the distances between each point in each cluster (at a certain collect). Hopefully, this can help us make informed decisions about the effectiveness of a chosen ```km_dist``` threshold

In [16]:
def print_cluster_distances(cluster):
    coords = cluster.get_coords()
    for i in range(len(coords)):
        for j in range(len(coords)):
            if i < j:
                print("Points " + str(i) + " and " + str(j))
                print("First point: " + str(coords[i].get_coords()))
                print("Second point: " + str(coords[j].get_coords()))
                dist = distance(coords[i].get_coords(), coords[j].get_coords()).km
                print("Distance in km between the points: " + str(dist))
                print()

In [17]:
collects[76].print_cluster_distances()

# idx = 0
# for cluster in clusters:
#     print("INDEX OF CLUSTER IN ARRAY: " + str(idx))
#     print_cluster_distances(cluster)
#     print()
#     print()

INDEX OF CLUSTER IN ARRAY: 0
Points 0 and 1
First point: (29.8699546, 43.1158639)
Second point: (29.8699281, 43.1158783)
Distance in km between the points: 0.0032503168300706503

Points 0 and 2
First point: (29.8699546, 43.1158639)
Second point: (29.9167578, 43.026635)
Distance in km between the points: 10.059648780320899

Points 0 and 3
First point: (29.8699546, 43.1158639)
Second point: (29.9185782, 43.0774445)
Distance in km between the points: 6.543866773416501

Points 0 and 4
First point: (29.8699546, 43.1158639)
Second point: (29.9168138, 43.0266163)
Distance in km between the points: 10.064396679734479

Points 0 and 5
First point: (29.8699546, 43.1158639)
Second point: (29.922788, 43.1119457)
Distance in km between the points: 5.868833748978102

Points 1 and 2
First point: (29.8699281, 43.1158783)
Second point: (29.9167578, 43.026635)
Distance in km between the points: 10.062356554784762

Points 1 and 3
First point: (29.8699281, 43.1158783)
Second point: (29.9185782, 43.0774445)

Distance in km between the points: 2.0936629768884054

Points 4 and 10
First point: (30.6403444, 42.3132286)
Second point: (30.5349312, 42.3380886)
Distance in km between the points: 11.927126536317976

Points 4 and 11
First point: (30.6403444, 42.3132286)
Second point: (30.481971, 42.4129877)
Distance in km between the points: 19.996706797661115

Points 4 and 12
First point: (30.6403444, 42.3132286)
Second point: (30.5190582, 42.3421302)
Distance in km between the points: 13.728875724367084

Points 4 and 13
First point: (30.6403444, 42.3132286)
Second point: (30.5914154, 42.3883806)
Distance in km between the points: 9.019415378962217

Points 4 and 14
First point: (30.6403444, 42.3132286)
Second point: (30.5349332, 42.3381192)
Distance in km between the points: 11.92749637280992

Points 4 and 15
First point: (30.6403444, 42.3132286)
Second point: (30.5953457, 42.4083835)
Distance in km between the points: 10.398536609169275

Points 4 and 16
First point: (30.6403444, 42.3132286)
Second

Distance in km between the points: 50.42596947959717

Points 4 and 84
First point: (30.6403444, 42.3132286)
Second point: (30.7759517, 42.2149839)
Distance in km between the points: 17.73678236614468

Points 4 and 85
First point: (30.6403444, 42.3132286)
Second point: (30.6523728, 42.1105181)
Distance in km between the points: 19.476493839707217

Points 5 and 6
First point: (30.6310546, 42.2645105)
Second point: (30.6182692, 42.2437976)
Distance in km between the points: 2.439837167543856

Points 5 and 7
First point: (30.6310546, 42.2645105)
Second point: (30.6716184, 42.189277)
Distance in km between the points: 8.498457877430432

Points 5 and 8
First point: (30.6310546, 42.2645105)
Second point: (30.65172, 42.1879924)
Distance in km between the points: 7.684477402950013

Points 5 and 9
First point: (30.6310546, 42.2645105)
Second point: (30.6408654, 42.2913962)
Distance in km between the points: 2.7974980980874458

Points 5 and 10
First point: (30.6310546, 42.2645105)
Second point: (

Distance in km between the points: 16.673280709612342

Points 9 and 59
First point: (30.6408654, 42.2913962)
Second point: (30.7456581, 42.2086232)
Distance in km between the points: 14.066377792246817

Points 9 and 60
First point: (30.6408654, 42.2913962)
Second point: (30.8223067, 41.9621215)
Distance in km between the points: 37.40424884129016

Points 9 and 61
First point: (30.6408654, 42.2913962)
Second point: (30.8842179, 41.9287493)
Distance in km between the points: 43.96987117469313

Points 9 and 62
First point: (30.6408654, 42.2913962)
Second point: (30.8598343, 42.0465252)
Distance in km between the points: 33.750293478359836

Points 9 and 63
First point: (30.6408654, 42.2913962)
Second point: (30.8334742, 41.9525127)
Distance in km between the points: 38.84823155265318

Points 9 and 64
First point: (30.6408654, 42.2913962)
Second point: (30.8699195, 41.9728586)
Distance in km between the points: 39.68693652621986

Points 9 and 65
First point: (30.6408654, 42.2913962)
Second 

Distance in km between the points: 25.167330936053997

Points 10 and 58
First point: (30.5349312, 42.3380886)
Second point: (30.775983, 42.2149653)
Distance in km between the points: 29.213434240068395

Points 10 and 59
First point: (30.5349312, 42.3380886)
Second point: (30.7456581, 42.2086232)
Distance in km between the points: 26.453765204638334

Points 10 and 60
First point: (30.5349312, 42.3380886)
Second point: (30.8223067, 41.9621215)
Distance in km between the points: 48.09284511971799

Points 10 and 61
First point: (30.5349312, 42.3380886)
Second point: (30.8842179, 41.9287493)
Distance in km between the points: 55.109426007133564

Points 10 and 62
First point: (30.5349312, 42.3380886)
Second point: (30.8598343, 42.0465252)
Distance in km between the points: 45.58183815474821

Points 10 and 63
First point: (30.5349312, 42.3380886)
Second point: (30.8334742, 41.9525127)
Distance in km between the points: 49.60219093136032

Points 10 and 64
First point: (30.5349312, 42.3380886)


...

Distance in km between the points: 29.083567252076882

Points 39 and 76
First point: (30.6871064, 42.1755308)
Second point: (30.7973027, 42.147639)
Distance in km between the points: 12.505475328936857

Points 39 and 77
First point: (30.6871064, 42.1755308)
Second point: (30.8406071, 42.0769876)
Distance in km between the points: 19.458095608797496

Points 39 and 78
First point: (30.6871064, 42.1755308)
Second point: (30.7980927, 42.175569)
Distance in km between the points: 12.304502384638658

Points 39 and 79
First point: (30.6871064, 42.1755308)
Second point: (30.7990088, 42.1753642)
Distance in km between the points: 12.406076448981597

Points 39 and 80
First point: (30.6871064, 42.1755308)
Second point: (30.7973623, 42.1476058)
Distance in km between the points: 12.512609435932017

Points 39 and 81
First point: (30.6871064, 42.1755308)
Second point: (30.7600732, 42.1919823)
Distance in km between the points: 8.241477130669567

Points 39 and 82
First point: (30.6871064, 42.1755308)

Distance in km between the points: 14.064682076479828

Points 48 and 60
First point: (30.6408848, 42.2913977)
Second point: (30.8223067, 41.9621215)
Distance in km between the points: 37.403210703457546

Points 48 and 61
First point: (30.6408848, 42.2913977)
Second point: (30.8842179, 41.9287493)
Distance in km between the points: 43.96866219406501

Points 48 and 62
First point: (30.6408848, 42.2913977)
Second point: (30.8598343, 42.0465252)
Distance in km between the points: 33.748844670273584

Points 48 and 63
First point: (30.6408848, 42.2913977)
Second point: (30.8334742, 41.9525127)
Distance in km between the points: 38.847166694239235

Points 48 and 64
First point: (30.6408848, 42.2913977)
Second point: (30.8699195, 41.9728586)
Distance in km between the points: 39.685668410130724

Points 48 and 65
First point: (30.6408848, 42.2913977)
Second point: (30.7524522, 42.0460538)
Distance in km between the points: 26.560936074531398

Points 48 and 66
First point: (30.6408848, 42.291397

Distance in km between the points: 12.750790358289018

Points 50 and 80
First point: (30.6992845, 42.2417019)
Second point: (30.7973623, 42.1476058)
Distance in km between the points: 14.121359099128668

Points 50 and 81
First point: (30.6992845, 42.2417019)
Second point: (30.7600732, 42.1919823)
Distance in km between the points: 8.251851687496895

Points 50 and 82
First point: (30.6992845, 42.2417019)
Second point: (30.9126577, 41.8913186)
Distance in km between the points: 41.03536825418816

Points 50 and 83
First point: (30.6992845, 42.2417019)
Second point: (30.912669, 41.8913078)
Distance in km between the points: 41.03693337178113

Points 50 and 84
First point: (30.6992845, 42.2417019)
Second point: (30.7759517, 42.2149839)
Distance in km between the points: 8.87646671704142

Points 50 and 85
First point: (30.6992845, 42.2417019)
Second point: (30.6523728, 42.1105181)
Distance in km between the points: 13.604164165486829

Points 51 and 52
First point: (30.6871754, 42.1752498)
Se

Distance in km between the points: 24.320554236268528

Points 63 and 82
First point: (30.8334742, 41.9525127)
Second point: (30.9126577, 41.8913186)
Distance in km between the points: 10.550571289890565

Points 63 and 83
First point: (30.8334742, 41.9525127)
Second point: (30.912669, 41.8913078)
Distance in km between the points: 10.55218639235439

Points 63 and 84
First point: (30.8334742, 41.9525127)
Second point: (30.7759517, 42.2149839)
Distance in km between the points: 25.914981503758668

Points 63 and 85
First point: (30.8334742, 41.9525127)
Second point: (30.6523728, 42.1105181)
Distance in km between the points: 25.14062285660946

Points 64 and 65
First point: (30.8699195, 41.9728586)
Second point: (30.7524522, 42.0460538)
Distance in km between the points: 14.78719796322329

Points 64 and 66
First point: (30.8699195, 41.9728586)
Second point: (30.8022632, 42.1143506)
Distance in km between the points: 15.475452214957851

Points 64 and 67
First point: (30.8699195, 41.9728586)


Distance in km between the points: 23.118650259047463

Points 67 and 83
First point: (30.75248, 42.0460417)
Second point: (30.912669, 41.8913078)
Distance in km between the points: 23.120273601639475

Points 67 and 84
First point: (30.75248, 42.0460417)
Second point: (30.7759517, 42.2149839)
Distance in km between the points: 16.382251288133798

Points 67 and 85
First point: (30.75248, 42.0460417)
Second point: (30.6523728, 42.1105181)
Distance in km between the points: 12.701404849846194

Points 68 and 69
First point: (30.7579848, 42.1162556)
Second point: (30.7681894, 41.9602129)
Distance in km between the points: 14.982233435783614

Points 68 and 70
First point: (30.7579848, 42.1162556)
Second point: (30.8023158, 42.114345)
Distance in km between the points: 4.918188669614618

Points 68 and 71
First point: (30.7579848, 42.1162556)
Second point: (30.8267149, 42.0233584)
Distance in km between the points: 11.709651652861556

Points 68 and 72
First point: (30.7579848, 42.1162556)
Secon

## I now make new cluster properties in order to create visual representations of clusters

In [18]:
collects[76].make_circle_properties()

# for cluster in clusters:
#     cluster.make_centroid()
#     cluster.make_radii()
#     print(cluster.get_centroid())
#     print(cluster.get_max_r())
#     print(cluster.get_avg_r())
#     print()
    


(29.90247008333333, 43.07906395)
5.308761134681347
4.404539794164294

(29.9988266, 42.82651)
0.9999214131420994
0.9999055068232111

(30.235994266666665, 42.6582736)
1.386968699693318
0.9246330886742222

(30.3195772, 42.7587519)
2.228654778080279
2.2285691859507377

(30.652004277906975, 42.226976768604644)
43.21455807158028
17.97573784414984

(31.00702005, 42.64787185)
0.00043449756586965224
0.0004344975656492901

(31.032393300000003, 42.5302904)
3.793808443100662
3.793800080796334

(31.080441399999998, 42.8210056)
3.9968016669588318
3.9967405748060263

(31.36368968, 41.71450848)
8.136246576000955
3.809911108451021

(31.3857338, 41.456161)
1.4578250996446305
0.5451900368418058

(31.433564333333333, 41.823119600000005)
1.9696084336935382
1.3130462650402268

(31.51743485, 41.93811855)
2.245074999203456
2.245052381419604

(31.296918425, 42.647476174999994)
2.9241858068454865
2.919764289410056

(31.260126166666666, 42.07115146666666)
2.4940182810479747
1.6627064398278655

(31.51890643333333

## Finally, using Leaflet and the ```folium``` module, I graph the clusters as red circles

In [19]:
import folium
import webbrowser
import os

In [20]:
def make_map(collect):
    os.chdir("map_outputs")
    m = folium.Map(location=[31.634036, 42.556084], zoom_start=8)
    cnt = 0
    for cluster in collect.get_clusters():
        r = cluster.get_max_r() * 1000
        c = cluster.get_centroid()
        folium.Circle(
            location = c,
            radius = r,
            color = 'crimson',
            fill = True,
            fill_color = 'crimson',
            popup = str(cnt)
        ).add_to(m)
        cnt += 1
    m.save('map.html')
    
    url = "file:///home/conor/Projects/D4D/spotthedifference/conor/map_outputs/map.html"

    webbrowser.open(url, new=2) # open in new tab
    
    os.chdir("..")

In [21]:
make_map(collects[76])